In [1]:
import pandas as pd
import folium
from folium.plugins import MarkerCluster
import math

In [2]:
railroad_lines = pd.read_csv("out.csv")

#for index, row in railroad_lines.iterrows():
#    print(row["internmediate"])
#    break

/Users/abhinavjain/anaconda/lib/python3.6/site-packages/IPython/core/interactiveshell.py:2717: DtypeWarning: Columns (11,25,26,27,28,29,30) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [3]:
railroad_lines.columns
NY_railroad_lines = railroad_lines[railroad_lines["STATE"] == "NY"]

In [6]:
US_center = [39.8283, -98.5795]
my_map = folium.Map(location = US_center, zoom_start = 4)

for index, row in NY_railroad_lines.iterrows():
    start = row["start"]
    end = row["end"]
    intermediates= row["internmediate"]
    all_points = []
    
    coords = []
    coords.append(float(start.split(",")[1]))
    coords.append(float(start.split(",")[0]))
    all_points.append(coords)
    
    try:
        if ";" in intermediates:
            intermediate_coords = intermediates.split(";")
        else:
            intermediate_coords = [intermediates]
    except TypeError:
        intermediate_coords = []
        
    for intermediate_coord in intermediate_coords:
        coords = []
        coords.append(float(intermediate_coord.split(",")[1]))
        coords.append(float(intermediate_coord.split(",")[0]))
        #folium.Marker(coords, popup = str(row["OBJECTID"])).add_to(my_map)
        all_points.append(coords)
            
    coords = []
    coords.append(float(end.split(",")[1]))
    coords.append(float(end.split(",")[0]))
    all_points.append(coords)
    if (index/1000 == 0):
        print(index)
    folium.PolyLine(all_points, color="brown", weight=2.5, opacity=1).add_to(my_map)

my_map    

In [7]:
#ND_railroad_lines = railroad_lines[railroad_lines["STATE"] == "ND"]
#ND_railroad_lines.to_csv("ND_railroad_lines.csv", index = False)

In [9]:
#len(ND_railroad_lines)
#ND_railroad_lines_start_end = ND_railroad_lines[["start","end","MILES"]]
#print(ND_railroad_lines_start_end.count())
#len(ND_railroad_lines_0_miles)
#ND_railroad_lines_start_end = ND_railroad_lines_start_end.drop_duplicates(subset = ["start","end"])
#ND_railroad_lines_start_end.MILES.fillna(0.001, inplace=True)
#print(ND_railroad_lines_start_end.count())

start    2618
end      2618
MILES    2618
dtype: int64
start    2618
end      2618
MILES    2618
dtype: int64


In [5]:
import networkx as nx
#G=nx.Graph()
G=nx.MultiGraph()
for index, row in railroad_lines.iterrows():
    G.add_edge(row["start"], row["end"], weight = float(row["MILES"]), key=row["OBJECTID"])

In [6]:
edges_list = G.edges()
count = 0
for edge in edges_list:
    count += 1
    #print(edge)
count

235090

In [12]:
src = "-73.11434638355172,40.9289772830384"
tgt = "-74.010721672271856,40.656227140295165"
p = nx.dijkstra_path(G, source=src, target=tgt)

In [13]:
len(p)

56

In [14]:
p

['-73.11434638355172,40.9289772830384',
 '-73.157692534038162,40.883496710028247',
 '-73.345594928766545,40.873608207253341',
 '-73.364713408242451,40.868044865234076',
 '-73.393719732983882,40.858255147145009',
 '-73.417115598177318,40.848438098982115',
 '-73.453957696275083,40.83202183211651',
 '-73.502333544580026,40.82386704999648',
 '-73.525617743793759,40.767849066083279',
 '-73.548279753672006,40.762368418747577',
 '-73.595240023277526,40.751229334203984',
 '-73.638860202146432,40.740796938850707',
 '-73.639647249404518,40.740611043190832',
 '-73.682808292145211,40.73031916719399',
 '-73.704784587424371,40.725106481149581',
 '-73.729230395437042,40.719239183949995',
 '-73.732351862284602,40.718489994163463',
 '-73.737872793934784,40.717164901100958',
 '-73.764631442207175,40.710742495997707',
 '-73.782676248068995,40.706411518018044',
 '-73.786770106177329,40.705428892048651',
 '-73.801318960007492,40.701874056725643',
 '-73.803271686331072,40.700962796805456',
 '-73.80410660301

In [23]:
import folium
from folium.plugins import MarkerCluster
import math

US_center = [39.8283, -98.5795]
my_map = folium.Map(location = US_center, zoom_start = 4)

all_points = []
i = 0
while i < len(p) - 1:
    #print(i)
    node = railroad_lines[railroad_lines["start"] == p[i]]
    node = node[node["end"] == p[i + 1]]
    node = node[node["MILES"] == node["MILES"].min()]
    flip = False
    if len(node) > 1:
        node = node.loc[[0]]
        #print("Multiple paths found for same node pair")
        #for index, row in node.iterrows():
         #   print(row["MILES"])
    elif len(node) == 0:
        #print("Zero paths found for same node pair. Flipping start and end and checking again.")
        node = railroad_lines[railroad_lines["end"] == p[i]]
        node = node[node["start"] == p[i + 1]]
        node = node[node["MILES"] == node["MILES"].min()]
        flip = True
        #print(len(node))
    
    node.internmediate.fillna("")
        
    for index, row in node.iterrows():
        if flip == True:
            end = row["start"]
            start = row["end"]
        else:
            start = row["start"]
            end = row["end"]
        intermediates = row["internmediate"]

        #if math.isnan(intermediates):
        #    intermediate_coords = []
        #else:
        try:
            if ";" in intermediates:
                intermediate_coords = intermediates.split(";")
            else:
                intermediate_coords = [intermediates]
        except TypeError:
            intermediate_coords = []
            
        
        
        coords = []
        coords.append(float(start.split(",")[1]))
        coords.append(float(start.split(",")[0]))
        #folium.Marker(coords, popup = str(row["OBJECTID"])).add_to(my_map)
        all_points.append(coords)
        #print("start:",start)
        
        #print(intermediates)
        if flip == True:
            intermediate_coords.reverse()

        for intermediate_coord in intermediate_coords:
            coords = []
            coords.append(float(intermediate_coord.split(",")[1]))
            coords.append(float(intermediate_coord.split(",")[0]))
            #folium.Marker(coords, popup = str(row["OBJECTID"])).add_to(my_map)
            all_points.append(coords)
        
        coords = []
        coords.append(float(end.split(",")[1]))
        coords.append(float(end.split(",")[0]))
        #folium.Marker(coords, popup = str(row["OBJECTID"])).add_to(my_map)
        all_points.append(coords)
        #print("end:",end)
    i += 1
    
coords = []
coords.append(float(src.split(",")[1]))
coords.append(float(src.split(",")[0]))
folium.Marker(coords, popup = "source").add_to(my_map)

coords = []
coords.append(float(tgt.split(",")[1]))
coords.append(float(tgt.split(",")[0]))
folium.Marker(coords, popup = "destination").add_to(my_map)

folium.PolyLine(all_points, color="red", weight=4.0, opacity=1).add_to(my_map)
#node0 = ND_railroad_lines[ND_railroad_lines["start"] == p[0]]
#node0 = node0[node0["end"] == p[1]]

In [24]:
my_map